<a href="https://colab.research.google.com/github/Tanishqchahal/Food-delivery-time-prediction/blob/main/FoodDeliveryTimePred.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [30]:
import pandas as pd
import numpy as np
import plotly.express as px

In [2]:
data = pd.read_csv('deliverytime.txt')
data.head()

ID Delivery_person_ID  Delivery_person_Age  Delivery_person_Ratings  \
0  4607     INDORES13DEL02                   37                      4.9   
1  B379     BANGRES18DEL02                   34                      4.5   
2  5D6D     BANGRES19DEL01                   23                      4.4   
3  7A6A    COIMBRES13DEL02                   38                      4.7   
4  70A2     CHENRES12DEL01                   32                      4.6   

   Restaurant_latitude  Restaurant_longitude  Delivery_location_latitude  \
0            22.745049             75.892471                   22.765049   
1            12.913041             77.683237                   13.043041   
2            12.914264             77.678400                   12.924264   
3            11.003669             76.976494                   11.053669   
4            12.972793             80.249982                   13.012793   

   Delivery_location_longitude Type_of_order Type_of_vehicle  Time_taken(min)  
0                    75.912471        Snack      motorcycle                24  
1                    77.813237        Snack         scooter                33  
2                    77.688400       Drinks      motorcycle                26  
3                    77.026494       Buffet      motorcycle                21  
4                    80.289982        Snack         scooter                30

In [3]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45593 entries, 0 to 45592
Data columns (total 11 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   ID                           45593 non-null  object 
 1   Delivery_person_ID           45593 non-null  object 
 2   Delivery_person_Age          45593 non-null  int64  
 3   Delivery_person_Ratings      45593 non-null  float64
 4   Restaurant_latitude          45593 non-null  float64
 5   Restaurant_longitude         45593 non-null  float64
 6   Delivery_location_latitude   45593 non-null  float64
 7   Delivery_location_longitude  45593 non-null  float64
 8   Type_of_order                45593 non-null  object 
 9   Type_of_vehicle              45593 non-null  object 
 10  Time_taken(min)              45593 non-null  int64  
dtypes: float64(5), int64(2), object(4)
memory usage: 3.8+ MB


In [4]:
data.isnull().sum()

ID                             0
Delivery_person_ID             0
Delivery_person_Age            0
Delivery_person_Ratings        0
Restaurant_latitude            0
Restaurant_longitude           0
Delivery_location_latitude     0
Delivery_location_longitude    0
Type_of_order                  0
Type_of_vehicle                0
Time_taken(min)                0
dtype: int64

##Use haversine to calculate distance between the restaurent and delivery destination using latitude and longitudes.

In [ ]:
pip install haversine

In [10]:
from haversine import haversine

In [ ]:
data['distance'] = np.nan

for i in range(len(data)):
  data['distance'][i] = haversine((data['Restaurant_latitude'][i],data['Restaurant_longitude'][i]), (data['Delivery_location_latitude'][i], data['Delivery_location_longitude'][i]))

##Reationship between distance and time taken

In [33]:
figure = px.scatter(data_frame = data, x='distance', y='Time_taken(min)', size='Time_taken(min)', trendline='ols', title='Reationship between distance and time taken')

figure.show()

There is constant relationship between distnace and time taken. Most deliveries take 25 to 35 minutes, no matter what the distance.

##Relationship between Delivery person's age and time taken

In [35]:
figure = px.scatter(data_frame= data, x='Delivery_person_Age', y= 'Time_taken(min)', size= 'Time_taken(min)', color='distance', trendline = 'ols', title="Relationship between age and time taken")

figure.show()

There is a slight positive relation between the age of delivery person and time taken for delivery. This shows that younger delivery partners take lesser time than older partners.

##Relationship between ratings and time taken

In [36]:
figure = px.scatter(data_frame= data, x= 'Delivery_person_Ratings', y= 'Time_taken(min)', size='Time_taken(min)', color= 'distance', trendline= 'ols', title= 'Relationship between ratings and time taken')

figure.show()

There is a negative relationship between ratings and time taken, ehich shoes that delivery partners with higher ratings take less time to deliver.

##Relationship between type of vehicle and time taken

In [38]:
figure = px.box(data, x= 'Type_of_vehicle', y= 'Time_taken(min)', color= 'Type_of_order')

figure.show()

This shows that the type of vehicle does not affect the delivery time

#LSTM Neural Network Model for Delivery Time Prediction

We will use the ratings, age and distance between the restaurent and delivery location to calculate the time taken.

##Splitting data

In [41]:
from sklearn.model_selection import train_test_split

x = np.array(data[['Delivery_person_Age', 'Delivery_person_Ratings', 'distance']])
y = np.array(data['Time_taken(min)'])

xtrain, xtest, ytrain, ytest = train_test_split(x, y, test_size=0.15, random_state=42)

##Building LSTM Model

In [43]:
from keras.models import Sequential
from keras.layers import LSTM, Dense

In [44]:
model = Sequential()
model.add(LSTM(128, return_sequences= True, input_shape= (xtrain.shape[1],1)))
model.add(LSTM(64, return_sequences= False))
model.add(Dense(25))
model.add(Dense(1))

In [45]:
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm (LSTM)                 (None, 3, 128)            66560     
                                                                 
 lstm_1 (LSTM)               (None, 64)                49408     
                                                                 
 dense (Dense)               (None, 25)                1625      
                                                                 
 dense_1 (Dense)             (None, 1)                 26        
                                                                 
Total params: 117619 (459.45 KB)
Trainable params: 117619 (459.45 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


##Train Model

In [47]:
model.compile(optimizer= 'adam', loss= 'mean_squared_error', metrics= ['accuracy'])
model.fit(xtrain, ytrain, batch_size=5, epochs= 11)

Epoch 1/11
7751/7751 [==============================] - 76s 9ms/step - loss: 65.2324 - accuracy: 0.0000e+00
Epoch 2/11
7751/7751 [==============================] - 68s 9ms/step - loss: 62.9346 - accuracy: 0.0000e+00
Epoch 3/11
7751/7751 [==============================] - 72s 9ms/step - loss: 60.8850 - accuracy: 0.0000e+00
Epoch 4/11
7751/7751 [==============================] - 69s 9ms/step - loss: 59.5846 - accuracy: 0.0000e+00
Epoch 5/11
7751/7751 [==============================] - 71s 9ms/step - loss: 58.8619 - accuracy: 0.0000e+00
Epoch 6/11
7751/7751 [==============================] - 71s 9ms/step - loss: 58.5552 - accuracy: 0.0000e+00
Epoch 7/11
7751/7751 [==============================] - 71s 9ms/step - loss: 58.3517 - accuracy: 0.0000e+00
Epoch 8/11
7751/7751 [==============================] - 70s 9ms/step - loss: 57.9744 - accuracy: 0.0000e+00
Epoch 9/11
7751/7751 [==============================] - 72s 9ms/step - loss: 57.7554 - accuracy: 0.0000e+00
Epoch 10/11
7751/7751 [=====

In [53]:
print('Food Delivery Time Prediction')

age = int(input("Enter Delivery Partner Age: "))
rating = float(input("Enter Delivery Partner Rating: "))
dist = float(input("Enter Distance:"))

features = np.array([[age,rating,dist]])
print(f'Predicted Delivery Time in minutes {model.predict(features)}')

Food Delivery Time Prediction
Enter Delivery Partner Age: 25
Enter Delivery Partner Rating: 7
Enter Distance:2.5
1/1 [==============================] - 0s 26ms/step
Predicted Delivery Time in minutes [[16.700426]]
